# 使用Folium 地圖做資料分析

Folium是Python上的地圖視覺化工具。透過Leaflet這個JavaScript Library以及OpenStreetMap地圖服務，可在Jupyter Notebook上實現互動式地圖繪製<br/>
安裝方法: conda install -c conda-forge folium  https://anaconda.org/conda-forge/folium

In [1]:
import numpy as np
import pandas as pd
import folium
from enum import Enum
from folium import plugins

# 使用資料: Kaggle上的 House Sales in King County, USA
連結: https://www.kaggle.com/sawayaka/kc-house

我將資料分成用臥室數、價格去做分類，並在地圖上以不同顏色標出不同房間數以及不同價格區間房子的地點

In [2]:
kc_house = pd.read_csv('kc_house_data.csv')

In [3]:
kc_house.head()

id             date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520  20141013T000000  221900.0         3       1.00         1180   
1  6414100192  20141209T000000  538000.0         3       2.25         2570   
2  5631500400  20150225T000000  180000.0         2       1.00          770   
3  2487200875  20141209T000000  604000.0         4       3.00         1960   
4  1954400510  20150218T000000  510000.0         3       2.00         1680   

   sqft_lot  floors  waterfront  view  ...  grade  sqft_above  sqft_basement  \
0      5650     1.0           0     0  ...      7        1180              0   
1      7242     2.0           0     0  ...      7        2170            400   
2     10000     1.0           0     0  ...      6         770              0   
3      5000     1.0           0     0  ...      7        1050            910   
4      8080     1.0           0     0  ...      8        1680              0   

   yr_built  yr_renovated  zipcode      lat     long  sqft_living15  \
0      1955             0    98178  47.5112 -122.257           1340   
1      1951          1991    98125  47.7210 -122.319           1690   
2      1933             0    98028  47.7379 -122.233           2720   
3      1965             0    98136  47.5208 -122.393           1360   
4      1987             0    98074  47.6168 -122.045           1800   

   sqft_lot15  
0        5650  
1        7639  
2        8062  
3        5000  
4        7503  

[5 rows x 21 columns]

# 臥室數

In [4]:
set(kc_house.bedrooms)

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 33}

# 取1000個點

In [5]:
kc_house =  kc_house.iloc[10000:11000,:]
kc_house.head()

id             date     price  bedrooms  bathrooms  \
10000  7818900060  20140708T000000  458400.0         4       2.50   
10001  2126059139  20150318T000000  620000.0         5       3.25   
10002  1759701600  20140512T000000  465000.0         3       1.50   
10003  1795920310  20140804T000000  690000.0         4       3.75   
10004  1626069139  20140821T000000  462500.0         3       2.25   

       sqft_living  sqft_lot  floors  waterfront  view  ...  grade  \
10000         1910     10300     1.0           0     0  ...      8   
10001         3160     10587     1.0           0     0  ...      7   
10002         2020     11358     1.0           0     0  ...      6   
10003         3210      7054     2.0           0     0  ...      8   
10004         2350     51400     1.0           0     0  ...      7   

       sqft_above  sqft_basement  yr_built  yr_renovated  zipcode      lat  \
10000        1910              0      1921          1968    98177  47.7581   
10001        2190            970      1960             0    98034  47.7238   
10002        1190            830      1956             0    98033  47.6641   
10003        3210              0      1985             0    98052  47.7268   
10004        1390            960      1977             0    98077  47.7417   

          long  sqft_living15  sqft_lot15  
10000 -122.359           1910        7750  
10001 -122.165           2200        7761  
10002 -122.185           2370        9520  
10003 -122.103           2350        8020  
10004 -122.053           2350       51400  

[5 rows x 21 columns]

# 初始的地圖

In [6]:
kc_map = folium.Map(location=[47.5,-122.2], zoom_start= 12)
kc_map

# 設定臥室數所代表的顏色

In [7]:
class Colors(Enum):
    peru = 0
    cyan = 1
    black = 2
    red = 3
    yellow = 4
    green = 5
    orange = 6
    violet = 7
    silver = 8
    navy = 9
    purple = 10
    pink = 11
    olive = 33

# 使用html 產生自訂的圖例

In [8]:
legend_html = '''
     <div style="position: fixed; 
     top: 0px; right: 0px; width: 100px; height:250px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     background-color:white;
     ">&nbsp; bedrooms  <br>
     &nbsp; 0&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:peru"></i><br>
     &nbsp; 1&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:cyan"></i>
     &nbsp; 2&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:black"></i>
     &nbsp; 3&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:red"></i>
     &nbsp; 4&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:yellow"></i>
     &nbsp; 5&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:green"></i>
     &nbsp; 6&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:orange"></i>
     &nbsp; 7&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:violet"></i>
     &nbsp; 8&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:silver"></i>
     &nbsp; 9&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:navy"></i>
     &nbsp; 10&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:purple"></i>
     &nbsp; 11&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:pink"></i>
     &nbsp; 33&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:olive"></i>
    </div>
     '''      

# 依不同臥室數以不同顏色將圖標標在地圖上

In [9]:
kc_map = folium.Map(location=[47.5,-122.2], zoom_start= 12)

for i in list(set(kc_house.bedrooms)):
    kc_bed = kc_house[kc_house.bedrooms == i]
    for lat, lng, label in zip(kc_bed.lat, kc_bed.long, kc_bed.bedrooms):
        folium.Marker([lat, lng], icon=folium.Icon(color= Colors(i).name, icon='home'), popup='bedroom:'+str(label),).add_to(kc_map)    
 
kc_map.get_root().html.add_child(folium.Element(legend_html))
kc_map

# 使用MarkerCluster 將座標點可以聚集避免圖標過多

In [10]:
kc_map = folium.Map(location = [47.5, -122.2], zoom_start = 12)

house = plugins.MarkerCluster().add_to(kc_map)

for i in list(set(kc_house.bedrooms)):
    kc_bed = kc_house[kc_house.bedrooms == i]
    for lat, lng, label in zip(kc_bed.lat, kc_bed.long, kc_bed.bedrooms):
        folium.Marker([lat, lng], icon=folium.Icon(color= Colors(i).name, icon='home'), popup='bedroom:'+str(label)).add_to(house)    
  
#匯入html
kc_map.get_root().html.add_child(folium.Element(legend_html))

kc_map

# 將地圖存成html檔來使用

In [11]:
kc_map.save('map.html')

In [12]:
kc_house = pd.read_csv('kc_house_data.csv')

# 依價格分類

In [13]:
_25price = kc_house.price.quantile(0.25)
_50price = kc_house.price.quantile(0.5)
_75price = kc_house.price.quantile(0.75)

# 價格區間的顏色

In [14]:
class Colors(Enum):
    red = 0
    yellow = 1
    green = 2
    violet = 3

In [15]:
legend_html = '''
     <div style="position: fixed; 
     top: 0px; right: 0px; width: 100px; height:150px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     background-color:white;
     ">&nbsp; price  <br>
     &nbsp; 25%以下&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:red"></i><br>
     &nbsp; 25%~50%&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:yellow"></i>
     &nbsp; 50%~75%&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:green"></i>
     &nbsp; 75%以上&nbsp; <i class="fa fa-map-marker fa-2x"
                  style="color:violet"></i>
    </div>
     '''  

In [16]:
kc_house =  kc_house.iloc[10000:11000,:]

In [17]:
def addMarker(kc_lat, kc_long, kc_item, idx):
    for lat, lng, label in zip(kc_lat, kc_long, kc_item):
        folium.Marker([lat, lng], icon=folium.Icon(color= Colors(idx).name, icon='home'), popup='price:'+str(label)).add_to(kc_map)    

In [21]:
kc_map = folium.Map(location=[47.5,-122.2], zoom_start= 12)

kc_25 = kc_house[kc_house.price<_25price]
addMarker(kc_25.lat, kc_25.long, kc_25.price, 0,)
kc_50 = kc_house[(kc_house.price>_25price) & (kc_house.price<_50price)]
addMarker(kc_50.lat, kc_50.long, kc_50.price, 1)
kc_75 = kc_house[(kc_house.price>_50price) & (kc_house.price<_75price)]
addMarker(kc_75.lat, kc_75.long, kc_75.price, 2)
kc_100 = kc_house[kc_house.price>_75price]
addMarker(kc_100.lat, kc_100.long, kc_100.price, 3)
    
kc_map.get_root().html.add_child(folium.Element(legend_html))
kc_map